# Άσκηση 11 Deep Learning on MNIST

Στην άσκηση αυτή θα συγκρίνουμε ένα βαθύ δίκτυο πρόσθιας τροφοδότησης με ένα συνελικτικό δίκτυο στο MNIST. 


![](https://miro.medium.com/max/990/0*94t_5cPF9mvBj20z.png)

Η συλλογή δεδομένων χειρόγραφων ψηφίων [MNIST](http://yann.lecun.com/exdb/mnist/) (Modified National Institute of Standards and Technology database) είναι από τα διασημότερα datasets της Μηχανικής Μάθησης. 

Έχει δημιουργηθεί από τους πρωτοπόρους της Τεχνητής Νοημοσύνης Yann LeCun, Corinna Cortes, και Chris Burges.

Ξεκινάμε, εισάγοντας τις βιβλιοθήκες που πρόκειται να χρησιμοποιήσουμε


In [ ]:
from sklearn.preprocessing import MinMaxScaler

import tensorflow as tf
import numpy as np
import matplotlib.pyplot as plt

print("Έκδοση Tensorflow: " + tf.__version__)

## Α. Φόρτωση και προεπεξεργασία των δεδομένων

### Α1. Μεταφόρτωση του dataset

Μεταφορτώστε το MNIST dataset τη μέθοδο [load_dataset()](https://www.tensorflow.org/api_docs/python/tf/keras/datasets/mnist/load_data) του submodule keras.datasets.mnist, όπως δείξαμε στο εργαστήριο

In [ ]:
(x_train, y_train), (x_test, y_test) = tf.keras.datasets.mnist.load_data()

### Α2. Μετατρέψετε τις δισδιάστατες εικόνες σε μονοδιάστατα διανύσματα

Με χρήση της μεθόδου [reshape()](https://numpy.org/doc/stable/reference/generated/numpy.ndarray.reshape.html?highlight=reshape#numpy.ndarray.reshape) του NumPy.

In [ ]:
x_train=x_train.reshape((x_train.shape[0], x_train.shape[1]*x_train.shape[2]))
x_test=x_test.reshape((x_test.shape[0], x_test.shape[1]*x_test.shape[2]))

### Α3. Κανονικοποιείστε γραμμικά τις τιμές των pixel στο $[0,1]$

Χρησιμοποιώντας την κλάση [MinMaxScaler](https://scikit-learn.org/stable/modules/generated/sklearn.preprocessing.MinMaxScaler.html) από το preprocessing module του scikit-learn.

In [ ]:
scaler = MinMaxScaler()
x_train = scaler.fit_transform(x_train)
x_test = scaler.fit_transform(x_test)

### Α4. Κωδικοποιείστε τις τιμές εξόδου σε μορφή διανύσματος one-hot

Με χρήση της μεθόδου [to_cetegorical()](https://www.tensorflow.org/api_docs/python/tf/keras/utils/to_categorical) του submodule keras.utils του Tensorflow.


In [ ]:
y_train = tf.keras.utils.to_categorical(y_train)
y_test = tf.keras.utils.to_categorical(y_test)

## Β. Βαθύ, πλήρως-συνδεδεμένο πολυεπίπεδο perceptron

Αρχικά, θα κατασκευάσουμε ένα πολυεπίπεδο percetpron με 5 επίπεδα (4 κρυφά και 1 επίπεδο εξόδου) για να επιλύσουμε το πρόβλημα ταξινόμησης στο MNIST dataset. Τα κρυφά επίπεδα θα επιλέξουμε να έχουν 200, 100, 60 και 30 νευρώνες αντίστοιχα και σιγμοειδή συνάρτηση ενεργοποίησης. Το επίπεδο εξόδου θα έχει συνάρτηση ενεργοποίησης την softmax.


### Β1. Κατασκευή δικτύου

Χρησιμοποιείστε την [ακολουθιακή διεπαφή](https://www.tensorflow.org/api_docs/python/tf/keras/Sequential) του keras. Αρχικοποιείστε τα βάρη όλων των επιπέδων χρησιμοποιώντας την [TruncatedNormal](https://www.tensorflow.org/api_docs/python/tf/keras/initializers/TruncatedNormal) από το submodule keras.initializers με μέση τιμή $0$ και τυπική απόκλιση $0.1$.



In [ ]:
mlp = tf.keras.Sequential([
  tf.keras.layers.Dense(
      200, 
      activation='sigmoid', 
      kernel_initializer=tf.keras.initializers.TruncatedNormal(mean=0., stddev=0.1) , 
      bias_initializer='zeros', 
      input_shape=(784,),
      name="Hidden1"
  ),
  tf.keras.layers.Dense(
      100, 
      activation='sigmoid', 
      kernel_initializer=tf.keras.initializers.TruncatedNormal(mean=0., stddev=0.1) , 
      bias_initializer='zeros', 
      name="Hidden2"
  ),
  tf.keras.layers.Dense(
      60, 
      activation='sigmoid', 
      kernel_initializer=tf.keras.initializers.TruncatedNormal(mean=0., stddev=0.1) , 
      bias_initializer='zeros', 
      name="Hidden3"
  ),
  tf.keras.layers.Dense(
      30, 
      activation='sigmoid', 
      kernel_initializer=tf.keras.initializers.TruncatedNormal(mean=0., stddev=0.1), 
      bias_initializer='zeros',
      name="Hidden4"
  ),
  tf.keras.layers.Dense(
      10, 
      activation='softmax', 
      kernel_initializer=tf.keras.initializers.TruncatedNormal(mean=0., stddev=0.1), 
      bias_initializer='zeros',
      name="Output"
  )
])

### Β2. Αρχιτεκτονική δικτύου


Εμφανίστε την αρχιτεκτονική του δικτύου, χρησιμοποιώντας τη μέθοδο *summary()*. Ποιο το πλήθος των εκπαιδεύσιμων παραμέτρων;



In [ ]:
mlp.summary()

Το πλήθος των εκπαιδεύσιμων παραμέτρων (βάρη, πολώσεις) είναι 185.000

### B3. Παράμετροι εκπαίδευσης του δικτύου

Ορίστε τις παραμέτρους εκπαίδευσης του δικτύου. Χρησιμοποιείστε συνάρτηση κόστους διασταυρούμενης επικύρωσης (cross-entropy loss), στοχαστική κατάβαση κλίσης και τη μετρική της ορθότητας (accuracy)

In [ ]:
mlp.compile(optimizer='sgd', loss='categorical_crossentropy', metrics=['accuracy'])

### B4. Εκπαιδεύστε το δίκτυο

Εκπαιδεύστε το δίκτυο στα δεδομένα εκπαίδευσης για 100 εποχές με μέγεθος δέσμης (`batch_size`) 64. 

In [ ]:
hist_mlp = mlp.fit(x_train, y_train, epochs=100, batch_size=64)

### Β5. Αποτελέσματα στο σύνολο εκπαίδευσης

Πόσο χρόνο διαρκεί περίπου η κάθε εποχή; Ποια είναι η αρχική και τελική τιμή της συνάρτησης κόστους και της ορθότητας; Τι παρατήρηση έχετε να κάνετε όσον αφορά την εκπαίδευση; Πως κρίνετε το αποτέλεσμα της εκπαίδευσης του συγκεκριμένου βαθιού, πλήρως διασυνδεδεμένου δικτύου 4 επιπέδων σε σύγκριση με το αντίστοιχο δίκτυο 2 επιπέδων που δείξαμε στο εργαστήριο;

In [ ]:
print(f"Αρχική τιμή συνάρτησης κόστους: {hist_mlp.history['loss'][0]:.4f}\tΤελική τιμή συνάρτησης κόστους: {hist_mlp.history['loss'][-1]:.4f}")
print(f"Αρχική τιμή ορθότητας: {hist_mlp.history['accuracy'][0]:.2%}\tΤελική τιμή ορθότητας: {hist_mlp.history['accuracy'][-1]:.2%}")

Η εκπαίδευση διαρκεί περίπου 4 δευτερόλεπτα ανά εποχή. Παρατηρούμε ότι για αρκετές εποχές στην αρχή, η εκπαίδευση παραμένει "κολλημένη", δηλαδή δεν βελτιώνεται ούτε η συνάρτηση κόστους ούτε η ορθότητα με το πέρας των εποχών. Τέλος, παρά την προσθήκη των 2 ακόμα κρυφών επιπέδων, η ορθότητα στο σύνολο εκπαίδευσης όχι μόνο δεν βελτιώθηκε, αλλά αντίθετα υστερεί (88% ενάντι 96%).

### Β6. Αποτελέσματα στο σύνολο ελέγχου

Ποια είναι η τιμή της ορθότητας στο σύνολο ελέγχου;

In [ ]:
_, mlp_acc = mlp.evaluate(x_test, y_test)

print('Ορθότητα στο σύνολο ελέγχου: {:.2%}'.format(mlp_acc))

### Β7. Βελτίωση απόδοσης

Με ποιον τρόπο θα μπορούσαμε να βελτιώσουμε την απόδοση του δικτύου;

Όπως είπαμε και στο εργαστήριο, ένας από τους λόγους που κολλάει η εκπαίδευση σχετίζεται με την αρχικοποίηση των παραμέτρων (βάρη και πολώσεις). Όσο το πλήθος τους αυξάνεται, θα πρέπει να γίνεται προσεκτικότερη η επιλογή τους. Στη συγκεκριμένη περίπτωση, αν αυξήσουμε το εύρος της τυπικής απόκλισης της Truncated Normal από $0.1$ σε $0.5$ παρατηρούμε ότι η εκπαίδευση πλέον δεν κολλάει.

In [ ]:
mlp = tf.keras.Sequential([
  tf.keras.layers.Dense(
      200, 
      activation='sigmoid', 
      kernel_initializer=tf.keras.initializers.TruncatedNormal(mean=0., stddev=0.5) , 
      bias_initializer='zeros', 
      input_shape=(784,),
      name="Hidden1"
  ),
  tf.keras.layers.Dense(
      100, 
      activation='sigmoid', 
      kernel_initializer=tf.keras.initializers.TruncatedNormal(mean=0., stddev=0.5) , 
      bias_initializer='zeros', 
      name="Hidden2"
  ),
  tf.keras.layers.Dense(
      60, 
      activation='sigmoid', 
      kernel_initializer=tf.keras.initializers.TruncatedNormal(mean=0., stddev=0.5) , 
      bias_initializer='zeros', 
      name="Hidden3"
  ),
  tf.keras.layers.Dense(
      30, 
      activation='sigmoid', 
      kernel_initializer=tf.keras.initializers.TruncatedNormal(mean=0., stddev=0.5), 
      bias_initializer='zeros',
      name="Hidden4"
  ),
  tf.keras.layers.Dense(
      10, 
      activation='softmax', 
      kernel_initializer=tf.keras.initializers.TruncatedNormal(mean=0., stddev=0.5), 
      bias_initializer='zeros',
      name="Output"
  )
])

mlp.compile(optimizer='sgd', loss='categorical_crossentropy', metrics=['accuracy'])

hist_mlp = mlp.fit(x_train, y_train, epochs=100, batch_size=64)

Πλέον στο σύνολο δεδομένων εκπαίδευσης έχουμε μια ορθότητα που πλησιάζει το 96%, ίδια με το πολυεπίπεδο perceptron των δύο κρυφών επιπέδων που είδαμε στο εργαστήριο. Για να βελτιώσουμε και άλλο την απόδοση του δικτύου που εξετάζουμε στη συγκεκριμένη άσκηση, θα πρέπει να κάνουμε άλλες επιλογές όσον αφορά το πλήθος των κρυφών επιπέδων, την γεωμετρία τους κλπ.

## Γ. Βαθύ συνελικτικό δίκτυο

Πριν προχωρήσουμε με το βαθύ συνελικτικό δίκτυο, θα μετασχηματίσουμε τα δεδομένα της εισόδου από διάνυσμα σε δισδιάστατη εικόνα 1 χρώματος.

In [ ]:
x_train = x_train.reshape((x_train.shape[0], 28, 28, 1))
x_test = x_test.reshape((x_test.shape[0], 28, 28, 1))

Στη συνέχεια θα φτιάξουμε ένα βαθύ συνελικτικό δίκτυο που θα αποτελείται από ένα επίπεδο δισδιάστατης συνέλιξης 32 φίλτρων διάστασης $6\times 6$ και ημιγραμμική συνάρτηση ενεργοποίησης ακολουθούμενο από ένα ακόμα επίπεδο δισδιάστατης συνέλιξης 64 φίλτρων διάστασης $3\times 3$ με ίδια τα υπόλοιπα χαρακτηριστικά. Κατόπιν, ακολουθεί ένα επίπεδο χωρικής υποδειγματοληψίας μέσης τιμής διάστασης $2\times 2$. Τέλος στο συνελικτικό δίκτυο θα προσθέσουμε και μια πλήρως διασυνδεδεμένη κεφαλή (head), αποτελούμενη από επίπεδο Flatten, ένα πυκνό επίπεδο 1024 νευρώνων με ημιγραμμική συνάρτηση ενεργοποίησης και το επίπεδο εξόδου 10 νευρώνων με συνάρτηση ενεργοποίησης softmax.


### Γ1. Κατασκευή δικτύου

Χρησιμοποιώντας την ακολουθιακή διεπαφή, κατασκευάστε το παραπάνω δίκτυο. Αρχικοποιείστε τα βάρη όλων των επιπέδων χρησιμοποιώντας την TruncatedNormal από το submodule keras.initializers με μέση τιμή $0$ και τυπική απόκλιση $0.1$ για τα συνελικτικά επίπεδα και τυπική απόκλιση $0.5$ για τα πυκνά επίπεδα. Τις πολώσεις αρχικοποιήστε τις σε σταθερή τιμή $0.1$ για τα συνελικτικά επίπεδα και $0.5$ για τα πυκνά επίπεδα, χρησιμοποιώντας την κλάση [Constant](https://www.tensorflow.org/api_docs/python/tf/keras/initializers/Constant) του submodule keras.initializers του tensorflow. Τέλος, στα συνελικτικά επίπεδα θεωρείστε ότι έχουμε βήμα 1 σε όλες τις διαστάσεις και same padding, ενώ στο επίπεδο υποδειγματοληψίας ([AveragePooling2D](https://www.tensorflow.org/api_docs/python/tf/keras/layers/AveragePooling2D)) χρησιμοποιείστε βήμα 2 σε όλες τις διαστάσεις (και same padding).

In [ ]:
cnn = tf.keras.models.Sequential([
    tf.keras.layers.Conv2D(
        filters=32, # 32 φίλτρα (kernels)
        kernel_size=(6, 6),  # 6x6 pixel μέγεθος kernel
        strides=(1, 1),  # 1 βήμα για όλες τις διαστάσεις εισόδου
        padding='same', # same padding για να μην αλλάξουν οι διαστάσεις
        activation='relu', 
        kernel_initializer=tf.keras.initializers.TruncatedNormal(mean=0., stddev=0.1),
        bias_initializer=tf.keras.initializers.Constant(0.1),
        input_shape=(28, 28, 1), #  εικόνα εισόδου 28x28 pixel, 1 κανάλι (χρώμα)
        name='Convolutional1'
    ),
    tf.keras.layers.Conv2D(
        filters=64, # 64 φίλτρα (kernels)
        kernel_size=(3, 3),  # 3x3 pixel μέγεθος kernel
        strides=(1, 1),  # 1 βήμα για όλες τις διαστάσεις εισόδου
        padding='same', # same padding για να μην αλλάξουν οι διαστάσεις
        activation='relu', 
        kernel_initializer=tf.keras.initializers.TruncatedNormal(mean=0., stddev=0.1),
        bias_initializer=tf.keras.initializers.Constant(0.1),
        name='Convolutional2'
    ),
    tf.keras.layers.AveragePooling2D(
        pool_size=(2, 2), # Παράθυρο μεγέθους 2x2
        strides=(2, 2), # Βήμα παραθύρου 2 (και στις 2 διαστάσεις)
        padding='same',
        name='Pooling1'
    ),
    tf.keras.layers.Flatten(name="Flatten"),
    tf.keras.layers.Dense(
        1024, 
        activation='relu', 
        kernel_initializer=tf.keras.initializers.TruncatedNormal(mean=0., stddev=0.5), 
        bias_initializer=tf.keras.initializers.Constant(0.5),
        name="Hidden1"
    ),
    tf.keras.layers.Dense(
      10, 
      activation='softmax', 
      kernel_initializer=tf.keras.initializers.TruncatedNormal(mean=0., stddev=0.5), 
      bias_initializer=tf.keras.initializers.Constant(0.5),
      name="Output"
    )
], name="ConvolutionalNetwork")



### Γ2. Αρχιτεκτονική δικτύου


Εμφανίστε την αρχιτκτονική του δικτύου, χρησιμοποιώντας τη μέθοδο *summary()*. Ποιο το πλήθος των εκπαιδεύσιμων παραμέτρων;


In [ ]:
cnn.summary()

Παρατηρούμε ότι το πλήθος των παραμέτρων είναι σχεδόν 12,9 εκατομμύρια. Ενώ στο συνελικτικό τμήμα του δικτύου (μέχρι το Flatten) έχουμε λίγες παραμέτρους εξαιτίας της ιδιότητας του διαμοιρασμού βαρών (weight sharing) της συνέλιξης, αυτές αυξάνουν κατά πολύ όταν περνάμε στο πλήρως συνδεδεμένο τμήμα του δικτύου, μιας και θα πρέπει να δοθούν ως είσοδος (με βάρος) σε κάθε έναν από τους 1.024 νευρώνες του πρώτου κρυφού επιπέδου.

### Γ3. Παράμετροι εκπαίδευσης του δικτύου

Ορίστε τις παραμέτρους εκπαίδευσης του δικτύου. Χρησιμοποιείστε συνάρτηση κόστους διασταυρούμενης επικύρωσης (cross-entropy loss), κατάβαση κλίσης [Adadelta](https://www.tensorflow.org/api_docs/python/tf/keras/optimizers/Adadelta) και τη μετρική της ορθότητας (accuracy)

In [ ]:
cnn.compile(optimizer='adadelta', loss='categorical_crossentropy', metrics=['accuracy'])

### Γ4. Εκπαιδεύστε το δίκτυο

Εκπαιδεύστε το δίκτυο στα δεδομένα εκπαίδευσης για 100 εποχές με μέγεθος δέσμης (`batch_size`) 64. 

In [ ]:
hist_cnn = cnn.fit(x_train, y_train, epochs=100, batch_size=64)

### Γ5. Αποτελέσματα στο σύνολο εκπαίδευσης

Πόσο χρόνο διαρκεί περίπου η κάθε εποχή; Ποια είναι η αρχική και τελική τιμή της συνάρτησης κόστους και της ορθότητας; Τι παρατήρηση έχετε να κάνετε όσον αφορά την εκπαίδευση;

In [ ]:
print(f"Αρχική τιμή συνάρτησης κόστους: {hist_cnn.history['loss'][0]:.4f}\tΤελική τιμή συνάρτησης κόστους: {hist_cnn.history['loss'][-1]:.4f}")
print(f"Αρχική τιμή ορθότητας: {hist_cnn.history['accuracy'][0]:.2%}\tΤελική τιμή ορθότητας: {hist_cnn.history['accuracy'][-1]:.2%}")

Τώρα πλέον η κάθε εποχή διαρκεί 17 με 18 sec (αντί 4 του βαθιού πολυεπίπεδου perceptron). Αυτό οφείλεται στο γεγονός ότι οι παράμετροι είναι κατά δύο τάξεις μεγέθους περισσότεροι (12,9 εκ. έναντι 185 χιλιάδων). Αν και στις πρώτες εποχές τόσο η συνάρτηση κόστους όσο και η ορθότητα βελτιώνονται γρήγορα, κατόπιν βελτιώνονται αρκετά αργά, επιτυγχάνοντας υποδεέστερη απόδοση όσον αφορά την ορθότητα στο σύνολο εκπαίδευσης σε σύγκριση με το συνελικτικό δίκτυο που εξετάσαμε στο εργαστήριο (93% έναντι 100%), αλλά και σε σύγκριση με το βαθύ πολυεπίπεδο perceptron που εξετάσαμε προηγουμένως.

### Γ6. Αποτελέσματα στο σύνολο ελέγχου

Ποια είναι η τιμή της ορθότητας στο σύνολο ελέγχου;

In [ ]:
_, cnn_acc = cnn.evaluate(x_test, y_test)

print('Ορθότητα στο σύνολο ελέγχου: {:.2%}'.format(cnn_acc))

## Δ. Συγκρίσεις

Συγκρίνετε τα δύο βαθιά δίκτυα (πολυεπίπεδο perceptron και συνελικτικό δίκτυο) στο συγκερκιμένο πρόβλημα

Το βαθύ συνελικτικό δίκτυο έχει πολύ μεγαλύτερο πλήθος παραμέτρων (δύο τάξεις μεγέθους περισσότερες). Έτσι η κάθε εποχή παίρνει περισσότερο χρόνο να ολοκληρωθεί. Επίσης, μετά τις πρώτες εποχές, συγκλίνει αργά, πράγμα που οφείλεται στο γεγονός ότι είναι "μεγάλο" για το συγκεκριμένο πρόβλημα (έχει 12,9 εκ. παραμέτρους έναντι 3,2 εκ. παραμέτρων του βαθιού συνελικτικού δικτύου που δείξαμε στο εργαστήριο). Συνεπώς, θα πρέπει να ελαττώσουμε το πλήθος των παραμέτρων του, εφαρμόζοντας επιπρόσθετη χωρική υποδειγματοληψία. Φυσικά, και σε αυτή την περίπτωση, θα μπορούσαμε να εξετάσουμε καλύτερη αρχικοποίηση των παραμέτρων του δικτύου καθώς και διαφορετικό αλγόριθμο μάθησης. 